In [1]:
import pandas as pd
import numpy as np 
import re, nltk
from numpy import array
from keras.preprocessing.text import one_hot
from keras.preprocessing.sequence import pad_sequences
from keras.models import Sequential
from keras.layers.core import Activation, Dropout, Dense
from keras.layers import Flatten 
from keras.layers.embeddings import Embedding
from sklearn.model_selection import train_test_split


In [2]:
import pandas as pd
df1= pd.read_csv(r'ALL_language.csv', encoding = "utf-8")
df = df1.sample(frac =1)
display(df)

English  \
3770   how warm is it in shanghai this weekend in deg...   
22320                               delete my 4 pm alarm   
17138                how fast is the wind in lehi utah ?   
21848                        show all alarms at midnight   
19100            what's the weather this week for hawaii   
...                                                  ...   
12765              what's the weather like on thursday ?   
6055                what is the high temperature today ?   
5719                    how's the weather in australia ?   
2882                 set the alarm for 24 hours from now   
18028                 cancel my alarm ( s ) for saturday   

                                         Amharic  \
3770   በዚህ ቅዳሜና እሁድ በ Shanghai ውስጥ ምን ያህል ሞቃት ነው   
22320                        የ 4 pm ማንቂያ ደወል ሰርዝ   
17138              በሊሂ ዩታ ውስጥ ነፋሱ ምን ያህል ፈጣን ነው?   
21848                 እኩለ ሌሊት ላይ ሁሉንም ማንቂያዎች አሳይ   
19100       በዚህ ሳምንት ለሃዋይ ምን ያህል የአየር ሁኔታ ምንድነው?   
...                                          ...   
12765              ሐሙስ ላይ ያለው የአየር ሁኔታ ምን ይመስላል?   
6055                     ዛሬ ከፍተኛ የሙቀት መጠን ምንድነው?   
5719          በአውስትራሊያ ውስጥ ያለው የአየር ሁኔታ እንዴት ነው?   
2882              ማንቂያውን ከአሁን ጀምሮ ለ 24 ሰዓታት ያዘጋጁ   
18028                  ለ ቅዳሜም የእኔን ማንቂያ (ቶች) ሰርዝ   

                                              Lithuanian  \
3770   Kaip šilta Šanchajuje šį savaitgalį Farenheito...   
22320                             Ištrinkite mano 16 val   
17138                      Kaip greitai vėjas Lehi Juta?   
21848               Parodykite visus aliarmus vidurnaktį   
19100                     Koks oras šią savaitę Havajams   
...                                                  ...   
12765                           Koks oras ketvirtadienį?   
6055                Kas šiandien yra aukšta temperatūra?   
5719                             Kaip oras Australijoje?   
2882         Nustatykite žadintuvą 24 valandas nuo dabar   
18028          Atšaukiu šeštadienį (-us) žadintuvą (-us)   

                                                  Arabic  \
3770   ما مدى دافئته في شنغهاي في نهاية هذا الأسبوع ب...   
22320                             حذف جهاز إنذار 4 مساءً   
17138                    ما مدى سرعة الريح في ليهي يوتا؟   
21848                 أظهر جميع الإنذارات في منتصف الليل   
19100                     ما هو الطقس هذا الأسبوع لهاواي   
...                                                  ...   
12765                         كيف يبدو الطقس يوم الخميس؟   
6055                  ما هي درجة الحرارة المرتفعة اليوم؟   
5719                          كيف حال الطقس في أستراليا؟   
2882                    اضبط المنبه لمدة 24 ساعة من الآن   
18028                    قم بإلغاء إنذاري (S) ليوم السبت   

                                                 Germany  Tigrinya  \
3770   Wie warm ist es in Shanghai an diesem Wochenen...       NaN   
22320                 Löschen Sie meinen Alarm um 16 Uhr       NaN   
17138             Wie schnell ist der Wind in Lehi Utah?       NaN   
21848              Zeigen Sie alle Alarme um Mitternacht       NaN   
19100     Was ist das Wetter in dieser Woche für Hawaii?       NaN   
...                                                  ...       ...   
12765                  Wie ist das Wetter am Donnerstag?       NaN   
6055                  Was ist die hohe Temperatur heute?       NaN   
5719                   Wie ist das Wetter in Australien?       NaN   
2882             Stellen Sie den Alarm in 24 Stunden ein       NaN   
18028        Stornieren Sie meine Alarm (en) für Samstag       NaN   

                                                  French  \
3770   Comme c'est chaud à Shanghai ce week-end en de...   
22320                       Supprimer mon alarme de 16 h   
17138         Quelle est la vitesse du vent à Lehi Utah?   
21848                Montrez toutes les alarmes à minuit   
19100        Quel temps fait-il cette semaine pour Hawaï   
...                                                  ...   


In [3]:
sentence = df.Czech .values.tolist()
sentiment = df.Intent.values.tolist()
print(len(sentence))
print(len(sentiment))

22994
22994


In [4]:
import pandas as pd
df2= pd.read_csv(r'Prompt2chatgpt.csv', encoding = "utf-8")
df3 = df2.sample(frac =1)
display(df3)

English  \
135             What time is the sunset in the spring?   
46   Set a daily alarm at 8:00 AM for the rest of t...   
118                     When does the sun set tonight?   
180               When does the sun rise this morning?   
32   Move my wake-up alarms to 6:45 AM starting nex...   
..                                                 ...   
186  When will the sun rise tomorrow on the east co...   
80           Extend the snooze duration by 14 minutes.   
116           When does the sun set in the wintertime?   
62                      Snooze for an extra 2 minutes.   
159                  What time did the sun rise today?   

                                               Amharic  \
135                       ከአንድ ጊዜ ጀምሮ ማታ ማታ ምን ሰዓት ነው?   
46                        መልስ እስከዚህ ድረስ በየ 30 ደቂቃው ደወል   
118                             በጣም ወቅት ፀሐይ ለምን ትጀምራለች   
180                    ለምን እንደምንለዋወጥ ምን ያህል ጊዜ ከፍ ብሏል?   
32                                      ሰኞ - አርብ ይድገሙት   
..                                                 ...   
186  ማህበረሰብ የምትዘምር በምሥራቅ ዳርቻ ላይ ነገ ፀሐይ ምን ያህል ጊዜ ይወጣል?   
80                                እባክዎን ለ 40 ደቂቃዎች ያሽጉ   
116                         ማህበረሰብ ሁሉ በምን ያህል ጊዜ ይጀምራል   
62                 ለ 25 ተጨማሪ ደቂቃዎች ለማሸለብ ማንቂያ ደወል ያዘጋጁ   
159          ዓመታዊ ጊዜ እንደምንለዋወጥ ጠዋት ፀሐይ ምን ያህል ጊዜ ይወጣል?   

                                               Germany  \
135             Wann spielt die Sonne heute im Winter?   
46     Wiederhole den Alarm bis zum Abschluss von 2017   
118                   Wann geht die Sonne heute unter?   
180  Um wie viel Uhr kommt die Sonne heute Morgen auf?   
32               Füge 10 Minuten zu meinem Alarm hinzu   
..                                                 ...   
186   Wie spät ist die Sonne heute Morgen aufgegangen?   
80           Stellen Sie den Alarm in den Snooze-Modus   
116   Um wie viel Uhr ist der heutige Sonnenuntergang?   
62          Setzen Sie den Alarm auf 15 Minuten Snooze   
159             Um wie viel Uhr ist der Sonnenaufgang?   

                                             Lithuania  \
135                      Kada yra saulėlydis šiandien?   
46      Pakartokite žadintuvą šeštadienį ir sekmadienį   
118                      Kada šiandien saulė nusileis?   
180                           Kada šį rytą kils saulė?   
32   Pakartokite aliarmą kas 2 valandas iki birželi...   
..                                                 ...   
186                Kada šiandien rytuose pakyla saulė?   
80       Nustatykite aliarmą į snaudimo režimą kasdien   
116           Kada šiandien šią vakarą saulė leisiasi?   
62   Nustatykite aliarmą, kad snaudžiate dar 25 min...   
159             Kiek laiko trunka saulėtekis šiandien?   

                                                French  \
135            Quand le soleil se couche-t-il en hiver   
46              Répète l'alarme jusqu'à la fin de 2017   
118                     Quand est le coucher du soleil   
180                Quelle heure est le lever du soleil   
32                      Ajoute 10 minutes à mon alarme   
..                                                 ...   
186     À quelle heure le soleil se lève-t-il ce matin   
80                     Définir l'alarme en mode snooze   
116   Quelle heure est le coucher du soleil de ce soir   
62   Réglez l'alarme pour répéter pendant 15 minute...   
159             Quand le soleil se couche-t-il ce soir   

                                                 Czech                 Intent  
135                         Kdy zapadalo slunce v zimě   weather__checkSunset  
46                   Opakujte alarm do konce roku 2017    alarm__modify_alarm  
118                                Kdy je západ slunce   weather__checkSunset  
180              V kolik hodin dnes ráno stoupá slunce  weather__checkSunrise  
32                    Přidejte do mého alarmu 10 minut    alarm__modify_alarm  
..                                                 ...                    ...  
18

In [6]:
sentence_1 = df3.Czech.values.tolist()
sentiment_1 = df3.Intent.values.tolist()
print(len(sentence_1))
print(len(sentiment_1))

189
189


In [7]:
for a in sentence_1:
    sentence.append(a)
for b in sentiment_1:
    sentiment.append(b)

print(len(sentiment))
print(len(sentence))

23183
23183


In [8]:
print(len(df.Intent.unique()))
print(df.Intent.value_counts())

13
weather__find                10461
reminder__set_reminder        4081
alarm__set_alarm              3915
alarm__cancel_alarm           1307
reminder__cancel_reminder      813
alarm__show_alarms             705
reminder__show_reminders       600
alarm__modify_alarm            399
alarm__time_left_on_alarm      270
alarm__snooze_alarm            260
weather__checkSunset           103
weather__checkSunrise           79
alarm__set_alar                  1
Name: Intent, dtype: int64


In [10]:
sentrp = sentence[0:18560]
sentsp = sentence[18400:23196]
semtr = sentiment[0:18560]
semts = sentiment[18400:23196]
print(len(sentrp))
print(len(sentsp))
print(len(semtr))
print(len(semts))

18560
4783
18560
4783


In [11]:
print(sentrp[0:10])
print(sentsp[0:10])
print(semtr[0:10])
print(semts[0:10])

['Jak teplé je to tento víkend v Šanghaji ve stupních Fahrenheitu', 'Smažte můj alarm ve 4:00', 'Jak rychle je vítr v Lehi Utah?', 'Zobrazit všechny alarmy o půlnoci', 'Jaké je počasí tento týden na Havaj', 'Nastavte alarm na 14:00', 'Mám si přinést bundu?', 'Alarm odložení po dobu 15 minut', 'Kdy bude příště pršet?', 'Bude to zítra horko?']
['Připomeňte si odejít za 30 minut a vyzvednout děti.', 'Musím prosím nastavit alarm na 17:00.', 'Nastavte připomenutí, abych odhodil mé děti ve škole v 8 hodin ráno.', 'Jaká je teplota právě teď?', 'Nastavte připomenutí pedikúry v sobotu', 'Otočení poplachu vloupání', 'Dej mi alarm každé dvě minuty na půl hodiny', 'dokončil moje připomenutí, prosím smažte', 'Nastavte alarm na 15:00 týdně od úterý s labelem „Wash Car“', 'Prší v Jižní Karolíně']
['weather__find', 'alarm__cancel_alarm', 'weather__find', 'alarm__show_alarms', 'weather__find', 'alarm__set_alarm', 'weather__find', 'alarm__snooze_alarm', 'weather__find', 'weather__find']
['reminder__set_

In [12]:
import numpy as np
import pandas as pd
from sentence_transformers import SentenceTransformer
import torch
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import matplotlib.pyplot as plt
import seaborn as sns
model = SentenceTransformer('sentence-transformers/LaBSE')
embeddingtr = model.encode(sentrp, batch_size = 128, convert_to_numpy = True, show_progress_bar = True)
embeddingts = model.encode(sentsp, batch_size = 128, convert_to_numpy = True, show_progress_bar = True)

Batches:   0%|          | 0/145 [00:00<?, ?it/s]

Batches:   0%|          | 0/38 [00:00<?, ?it/s]

In [13]:
from sklearn.metrics.pairwise import cosine_similarity
frames = []
for idx, val in enumerate(sentsp):
    cos_va = cosine_similarity(embeddingts, embeddingtr)[idx]
    df1 = pd.DataFrame(sentrp, columns =['sentenc'])
    df1['position'] = df1.index.values
    
    df1['realsem'] = semts[idx]
    df1['new_cosine'] = (cos_va)
    query_sentence_cosine_df1 = df1.sort_values('new_cosine', ascending = False)
    df2 = query_sentence_cosine_df1[['sentenc', 'new_cosine','position','realsem']].head(3)
    frames.append(df2)
    result = pd.concat(frames)
display(result)

sentenc  new_cosine  \
18400  Připomeňte si odejít za 30 minut a vyzvednout ...    1.000000   
8860   Nastavte připomenutí za 30 minut a vyzvedněte ...    0.732692   
11341       Připomeňte mi, abych psa nakrmil za 30 minut    0.727013   
18401              Musím prosím nastavit alarm na 17:00.    1.000000   
13329           Potřebuji, abys nastavil alarm na 13:00.    0.859495   
...                                                  ...         ...   
15849    Nastavte interval odložení na alarm na 15 minut    0.902025   
15236             Nastavte alarm, aby za 15 minut odešel    0.900030   
18518                           V kolik je východ slunce    1.000000   
9932                      V kolik hodin je východ slunce    0.978583   
10557                     V kolik hodin je východ slunce    0.978583   

       position                 realsem  
18400     18400  reminder__set_reminder  
8860       8860  reminder__set_reminder  
11341     11341  reminder__set_reminder  
18401     18401        alarm__set_alarm  
13329     13329        alarm__set_alarm  
...         ...                     ...  
15849     15849     alarm__snooze_alarm  
15236     15236     alarm__snooze_alarm  
18518     18518   weather__checkSunrise  
9932       9932   weather__checkSunrise  
10557     10557   weather__checkSunrise  

[14349 rows x 4 columns]

In [15]:
for i in result['position']:
    result['pred'][i]= semtr[i]
display(result)

C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppD

C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppD

C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppD

C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppD

C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppD

...

C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppD

C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppD

C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppD

C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppData\Local\Temp/ipykernel_27528/385415318.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['pred'][i]= semtr[i]
C:\Users\senug\AppD

sentenc  new_cosine  \
18400  Připomeňte si odejít za 30 minut a vyzvednout ...    1.000000   
8860   Nastavte připomenutí za 30 minut a vyzvedněte ...    0.732692   
11341       Připomeňte mi, abych psa nakrmil za 30 minut    0.727013   
18401              Musím prosím nastavit alarm na 17:00.    1.000000   
13329           Potřebuji, abys nastavil alarm na 13:00.    0.859495   
...                                                  ...         ...   
15849    Nastavte interval odložení na alarm na 15 minut    0.902025   
15236             Nastavte alarm, aby za 15 minut odešel    0.900030   
18518                           V kolik je východ slunce    1.000000   
9932                      V kolik hodin je východ slunce    0.978583   
10557                     V kolik hodin je východ slunce    0.978583   

       position                 realsem                    pred  
18400     18400  reminder__set_reminder  reminder__set_reminder  
8860       8860  reminder__set_reminder  reminder__set_reminder  
11341     11341  reminder__set_reminder  reminder__set_reminder  
18401     18401        alarm__set_alarm        alarm__set_alarm  
13329     13329        alarm__set_alarm        alarm__set_alarm  
...         ...                     ...                     ...  
15849     15849     alarm__snooze_alarm     alarm__snooze_alarm  
15236     15236     alarm__snooze_alarm        alarm__set_alarm  
18518     18518   weather__checkSunrise   weather__checkSunrise  
9932       9932   weather__checkSunrise   weather__checkSunrise  
10557     10557   weather__checkSunrise   weather__checkSunrise  

[14349 rows x 5 columns]

In [16]:
import numpy
Grp = []
subs = []
result['pred']
for i in result['pred']:
    Grp.append(i)
#print(Grp)
print(len(Grp))
print(type(Grp))
splits = np.array_split(Grp,len(sentsp))# no of testing sets
vote = []
for array in splits:
    vote.append(list(array))
print(vote)
gr = []
for el in vote:
    mx = max(set(el), key =el.count)
    gr.append(mx)
    
print(gr)
print(type(gr))
print(len(gr))

14349
<class 'list'>
[['reminder__set_reminder', 'reminder__set_reminder', 'reminder__set_reminder'], ['alarm__set_alarm', 'alarm__set_alarm', 'alarm__set_alarm'], ['reminder__set_reminder', 'reminder__set_reminder', 'alarm__set_alarm'], ['weather__find', 'weather__find', 'weather__find'], ['reminder__set_reminder', 'reminder__set_reminder', 'reminder__set_reminder'], ['alarm__cancel_alarm', 'alarm__snooze_alarm', 'alarm__snooze_alarm'], ['alarm__set_alarm', 'alarm__set_alarm', 'alarm__set_alarm'], ['reminder__cancel_reminder', 'reminder__cancel_reminder', 'reminder__cancel_reminder'], ['alarm__set_alarm', 'alarm__set_alarm', 'alarm__set_alarm'], ['weather__find', 'weather__find', 'weather__find'], ['reminder__set_reminder', 'reminder__set_reminder', 'reminder__set_reminder'], ['weather__find', 'weather__checkSunset', 'weather__checkSunset'], ['weather__find', 'weather__find', 'weather__find'], ['weather__find', 'weather__find', 'weather__find'], ['alarm__set_alarm', 'alarm__set_alarm'

In [17]:
from sklearn.metrics.pairwise import cosine_similarity
Fram = []
for idx, val in enumerate(sentsp):
    cos_va = cosine_similarity(embeddingts, embeddingtr)[idx]
    
    df1 = pd.DataFrame(sentrp, columns =['sentenc'])
    df1['position'] = df1.index.values
    df1['realsem'] = semts[idx]
    df1['new_cosine'] = (cos_va)
    query_sentence_cosine_df1 = df1.sort_values('new_cosine', ascending = False)
    res = query_sentence_cosine_df1[['sentenc', 'new_cosine','position','realsem']].head(1)
    Fram.append(res)
    reslt1= pd.concat(Fram)
display(reslt1)

sentenc  new_cosine  \
18400  Připomeňte si odejít za 30 minut a vyzvednout ...    1.000000   
18401              Musím prosím nastavit alarm na 17:00.    1.000000   
18402  Nastavte připomenutí, abych odhodil mé děti ve...    1.000000   
13168                         Jaká je teplota právě teď?    1.000000   
18404             Nastavte připomenutí pedikúry v sobotu    1.000000   
...                                                  ...         ...   
3152                          V kolik dnes slunce vstalo    1.000000   
1617                          Vypněte odložení pro alarm    0.823223   
3423                V kolik hodin je dnešní západ slunce    1.000000   
8916   Nastavte alarm, aby se odložil po dobu dalších...    1.000000   
18518                           V kolik je východ slunce    1.000000   

       position                 realsem  
18400     18400  reminder__set_reminder  
18401     18401        alarm__set_alarm  
18402     18402  reminder__set_reminder  
13168     13168           weather__find  
18404     18404  reminder__set_reminder  
...         ...                     ...  
3152       3152   weather__checkSunrise  
1617       1617     alarm__snooze_alarm  
3423       3423    weather__checkSunset  
8916       8916     alarm__snooze_alarm  
18518     18518   weather__checkSunrise  

[4783 rows x 4 columns]

In [18]:
reslt1['predic']= gr
display(reslt1) 

sentenc  new_cosine  \
18400  Připomeňte si odejít za 30 minut a vyzvednout ...    1.000000   
18401              Musím prosím nastavit alarm na 17:00.    1.000000   
18402  Nastavte připomenutí, abych odhodil mé děti ve...    1.000000   
13168                         Jaká je teplota právě teď?    1.000000   
18404             Nastavte připomenutí pedikúry v sobotu    1.000000   
...                                                  ...         ...   
3152                          V kolik dnes slunce vstalo    1.000000   
1617                          Vypněte odložení pro alarm    0.823223   
3423                V kolik hodin je dnešní západ slunce    1.000000   
8916   Nastavte alarm, aby se odložil po dobu dalších...    1.000000   
18518                           V kolik je východ slunce    1.000000   

       position                 realsem                  predic  
18400     18400  reminder__set_reminder  reminder__set_reminder  
18401     18401        alarm__set_alarm        alarm__set_alarm  
18402     18402  reminder__set_reminder  reminder__set_reminder  
13168     13168           weather__find           weather__find  
18404     18404  reminder__set_reminder  reminder__set_reminder  
...         ...                     ...                     ...  
3152       3152   weather__checkSunrise    weather__checkSunset  
1617       1617     alarm__snooze_alarm     alarm__snooze_alarm  
3423       3423    weather__checkSunset    weather__checkSunset  
8916       8916     alarm__snooze_alarm     alarm__snooze_alarm  
18518     18518   weather__checkSunrise   weather__checkSunrise  

[4783 rows x 5 columns]

In [19]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None):  # more options can be specified also
    display(reslt1)

sentenc  new_cosine  \
18400  Připomeňte si odejít za 30 minut a vyzvednout ...    1.000000   
18401              Musím prosím nastavit alarm na 17:00.    1.000000   
18402  Nastavte připomenutí, abych odhodil mé děti ve...    1.000000   
13168                         Jaká je teplota právě teď?    1.000000   
18404             Nastavte připomenutí pedikúry v sobotu    1.000000   
18405                          Otočení poplachu vloupání    1.000000   
18406        Dej mi alarm každé dvě minuty na půl hodiny    1.000000   
18407           dokončil moje připomenutí, prosím smažte    1.000000   
18408  Nastavte alarm na 15:00 týdně od úterý s label...    1.000000   
18409                              Prší v Jižní Karolíně    1.000000   
18410     Připomeňte mi, abych v pátek koupil dárek Kris    1.000000   
18411                          Kdy se dnes večer ztmavne    1.000000   
18412             Jaké je počasí v Portlandu tento týden    1.000000   
18413                                    je to zasněžené    1.000000   
3647            Nastavte alarm na 6:00 v pondělí - pátek    1.000000   
18415                            Řekni mi páteční počasí    1.000000   
18416  Nastavte denní připomenutí, abych si vzal mé l...    1.000000   
18417                              je pátek být slunečný    1.000000   
18418  Připomeňte mi, abych zítra ve 14:00 vyzvedl kr...    1.000000   
10743                        Jaká je dnes vysoká teplota    1.000000   
18420           Zrušte připomenutí jmenování mého lékaře    1.000000   
18421                         Nastavit alarm 7: 00 zítra    1.000000   
18422     Zrušte alarmy na příští týden kvůli přehlídce.    1.000000   
18423                 Jak teplé je dnes Šanghaj v Celsiu    1.000000   
18424                    Nastavte dnes večer připomenutí    1.000000   
18425                  Připomeňte mi, abych šel na poštu    1.000000   
18426                          Jaké je pro dnešek nízké?    1.000000   
18427                Nastavte alarm na 10:00 každý pátek    1.000000   
18428     Zrušte prosím alarm, který jsem právě nastavil    1.000000   
18429           V kolik hodin se očekává, že začne pršet    1.000000   
18430                    Chci víkendovou zprávu o počasí    1.000000   
18431                   Změňte alarm na 30 minut později    1.000000   
18432   Nastavte si můj alarm na tři hodiny od nynějška.    1.000000   
18433  Nastavte připomenutí pro uložení vajec pro Jen...    1.000000   
18434  Zítra mi dejte aktualizaci nebezpečného tepla ...    1.000000   
18435              Nastavte alarm na 10:00 každý čtvrtek    1.000000   
18436                    V sobotu bude v San Diegu horko    1.000000   
18437  Chceme mít dnes piknik, v kolik hodin bychom m...    1.000000   
13168                         Jaká je teplota právě teď?    1.000000   
18439                   Má to být dnes v Chicagu větrno?    1.000000   
18440  Připomeňte mi, abych si koupil krmivo pro psy ...    1.000000   
18441        Mám na tento víkend nastaveno nějaké alarmy    1.000000   
18442                     Kolik času na aktuálním alarmu    1.000000   
17862                           Ukaž mi moje připomenutí    1.000000   
18444                              Mám dnes nosit bundu?    1.000000   
15300                             Nastavte alarm na 3:00    1.000000   
18446                    Nastavte alarm na 20:00 a 22:00    1.000000   
18447  Nastavte alarm na 7: 55:00 každý den, abyste v...    1.000000   
18448                                Zrušit alarm večeře    1.000000   
18449           Zrušte mé připomenutí zavolat veterináře    1.000000   
18450                     Jak vlhké to bude tento týden?    1.000000   
18451                             Musím si přinést kabát    1.000000   
18452                   Jaká noc tento týden bude jasná?    1.000000   
18453               Zrušte všechna nastavená připomenutí    1.000000   
18454                 Nastavte alarm na 8 hodin v sobotu    1.000000   
18455     Zobrazi

In [20]:
import pandas as pd
true_class = reslt1["realsem"].to_numpy()
pred_class = reslt1["predic"].to_numpy()

In [21]:
Accuracy = sum(np.array(pred_class)==np.array(true_class))/float(len(true_class))
print(Accuracy)

0.9464771064185658


In [22]:
print(true_class)
print(pred_class)
print(true_class.dtype)
print(pred_class.dtype)
true_clas = true_class.astype(str)
pred_clas = pred_class.astype(str)
print(true_clas.dtype)
print(pred_clas.dtype)

['reminder__set_reminder' 'alarm__set_alarm' 'reminder__set_reminder' ...
 'weather__checkSunset' 'alarm__snooze_alarm' 'weather__checkSunrise']
['reminder__set_reminder' 'alarm__set_alarm' 'reminder__set_reminder' ...
 'weather__checkSunset' 'alarm__snooze_alarm' 'weather__checkSunrise']
object
object
<U25
<U25


In [23]:
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
cf_matrix = confusion_matrix(true_clas, pred_clas)
print(cf_matrix)

[[ 245    1   12    1    4    0    0    1    0    0    0    0    0]
 [   9   74   68    0    2    0    0    0    0   11    0    0    1]
 [  26    0  779    2    4    0    0    0    7    0    0    0    0]
 [   1    0    3  109    0    5    0    0    0    0    0    0    1]
 [   4    0    8    0   75    0    0    0    0    0    0    0    0]
 [   0    0    0    2    1   54    0    0    0    0    0    0    0]
 [   0    0    0    0    0    0    0    0    0    0    0    0    1]
 [   3    0    0    0    0    0    0  163   10    2    0    0    0]
 [   1    1   17    0    0    0    0    8  772    0    0    0    1]
 [   0    0    0    1    0    0    0    3   11  125    0    0    1]
 [   0    0    0    0    0    0    0    0    0    0   50   10    0]
 [   0    0    0    0    0    0    0    0    0    0    7   57    1]
 [   0    0    1    0    0    0    0    0    0    1    0    2 2024]]


In [24]:
from sklearn import metrics
print(metrics.classification_report(true_clas, pred_clas))

                           precision    recall  f1-score   support

      alarm__cancel_alarm       0.85      0.93      0.89       264
      alarm__modify_alarm       0.97      0.45      0.61       165
         alarm__set_alarm       0.88      0.95      0.91       818
       alarm__show_alarms       0.95      0.92      0.93       119
      alarm__snooze_alarm       0.87      0.86      0.87        87
alarm__time_left_on_alarm       0.92      0.95      0.93        57
                      nan       0.00      0.00      0.00         1
reminder__cancel_reminder       0.93      0.92      0.92       178
   reminder__set_reminder       0.96      0.96      0.96       800
 reminder__show_reminders       0.90      0.89      0.89       141
    weather__checkSunrise       0.88      0.83      0.85        60
     weather__checkSunset       0.83      0.88      0.85        65
            weather__find       1.00      1.00      1.00      2028

                 accuracy                           0.95    

C:\Users\senug\Anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\senug\Anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\senug\Anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
